# Building An Algorithm To Filter Out SMS Spam

Spam has been a frustrating nuisance since digital communication has been in existence. To save time and to avoid clicking on malicious links, we use spam filters. 

We will be using a dataset of [5,572 SMS messages](http://www.dt.fee.unicamp.br/~tiago/smsspamcollection/#composition) that have already been classified by humans as spam or non-spam (called "ham" in the dataset).  We'll use 80% of the data to train an algorithm to identify spam messages. The other 20% will be saved for testing our filter. The filter will be a [multinomial Naive Bayes classifier](https://en.wikipedia.org/wiki/Naive_Bayes_classifier#Multinomial_na%C3%AFve_Bayes) function. It will quickly identify incoming SMS messages as spam or non-spam (ham).

Our secondary goal is pedagogical: to explain how and why this algorithm works so that someone new to considering probabilities can gain an understanding. For this purpose I have written an extensive introduction to beginner probability concepts and from there derived the Naive Bayes algorithm. I used LaTeX in the markdown cells to render the mathematics.

Upon deriving the algorithm, we'll prepare our data, train the algorithm, and create a filter function. If you are already comfortable with this algorithm or uninterested in the details of its derivation, skip to the [reading in the data](#analysis_start) section. 

In the end, we'll see that the filter we create is successful 98% of the time in identifying spam and ham messages in the test data.

---
---

## Probability basics

The probability that a flipped coin will land with the heads side up is $1/2$ or $0.5$. The probability that an `event A` will happen is denoted by `P(A)`. In a coin flip, the probability of the coin landing with the heads side up is given by: $$P(\textrm{Heads}) = \frac{1}{2} = 0.5$$
Likewise, the probability of rolling a two on a six-sided die is: $$P(\textrm{Roll a 2}) = \frac{1}{6} = .1\overline{6}$$

We want to know the probability that we both get a heads from flipping a coin *and* a 2 from rolling a die. The coin and die have no effect on each other, so their probabilities are independent of one another. The probability of both of these independent events occuring is given by: 

$$P(A \textrm{ and } B) = P(A)*P(B)$$
For our specific case, we have: 

$$P(\textrm{Heads and Roll a 2}) = 0.5*0.16 = 0.083$$

When we write the probability of multiple events occuring, we connect the events with the intersection symbol $\cap$ which stands in for the "and" connector. We can now rewrite the previous formula:

$$P(A\cap B) = P(A)*P(B)$$

This is the probability that two independent events will both occur.

### Addition Rule
When we're interested in at least one of the events occuring, what we want to know is the probablility that `event A` *OR* `event B` occurs. We use the union symbol $\cup$ in place of the "or" connector. The probability that at least one of these events occurs will be given by the sum of each of their individual probabilities subtracted by the probability that they both occur. We subtract the probability that they both occur to avoid double counting it since it's a part of each of their individual probabilities.


$$P(A\cup B) = P(A) + P(B) - P(A\cap B)$$

This is known as the addition rule.

If the two events are **mutually exclusive**, meaning they can never occur together, then the probability of both events occuring is equal to 0: $P(A\cap B) = 0$. In cases of mutual exclusivity, the addition rule simplifies to: $P(A\cup B) = P(A) + P(B)$.

An example of mutually exclusive events is getting a heads and a tails on a single coin flip. $P(\textrm{Heads}\cap \textrm{Tails}) = 0$.


### Multiplication Rule - Conditional Probability

When two events are dependent on one another, the formula for finding the probability that they both occur changes accordingly. For example, `event A` is rolling a 2 on a six-sided fair die, and `event B` is rolling an even number on the same die during the same roll. 

$$P(2) = \frac{1}{6}$$
$$P(\textrm{even}) = \frac{1}{2}$$

We can write all possible outcomes of a single die roll as:

$$\Omega = \{1,2,3,4,5,6\}$$

We use $\Omega$ to indicate that this is a sample space, meaning the set of all possible outcomes. By looking at these possible outcomes, we can see that the probability that a single roll results in both a `2` and an `even` number is $\frac{1}{6}$. If, however, we use our original multiplication formula for independent events, the result would be $P(2\cap \textrm{even}) = \frac{1}{6}*\frac{1}{2} = \frac{1}{12}$.

To adjust this formula for dependent events, we need to consider the probability that `event A` occurs *given the condition* that `event B` occurs. We denote this expression mathematically as $P(A|B)$. The sample space for rolling an even number is $\Omega = \{2,4,6\}$. The probability that we `roll a 2` *given the condition* that we rolled an `even` number is therefore $\frac{1}{3}$. We can then multiply this probability by the probability that we roll an `even` number to find the true probability that our roll is both a `2` and `even`.

$$P(2|\textrm{even}) = \frac{1}{3}$$

$$P(2\cap \textrm{even}) = P(\textrm{even})*P(2|\textrm{even})$$

$$P(2\cap \textrm{even})= \frac{1}{2} * \frac{1}{3} = \frac{1}{6}$$

Written generally, the multiplication rule for conditional probability is:

$$P(A\cap B) = P(B)*P(A|B)$$



If any one of the three following conditions is true, then our events A and B are **statistically independent**:

$$P(A) = P(A|B)$$
$$P(B) = P(B|A)$$
$$P(A\cap B) = P(A)*P(B)$$

This shows why for independent events the multiplication rule simplifies to the original equation we used.

### Law of total probability

If we have two events, $B_1$ and $B_2$, using the multiplication rule for conditional probability we know:

$$P(A\cap B_1) = P(B_1)*P(A|B_1)$$

$$P(A\cap B_2) = P(B_2)*P(A|B_2)$$

If $B_1$ and $B_2$ are exhaustive, meaning they comprise the entire sample space $\Omega = \{B_1,B_2\}$ we get:

$$P(A) = P(A\cap B_1) + P(A\cap B_2)$$

As an example, consider flipping a coin twice. Event $A$ is getting a heads on the first flip. Event $B_1$ is getting a heads on the second flip. Event $B_2$ is getting a tails on the second flip. Events $B_1$ and $B_2$ are exhaustive because they contain all of the possible outcomes for the second coin flip. We can now rewrite our equation for the total probability of A:

$$P(A) = P(B_1)* P(A|B_1) + P(B_2)* P(A|B_2)$$

For three exhaustive events $B_1, B_2, B_3$, these equations become:

$$P(A) = P(A\cap B_1) + P(A\cap B_2)+ P(A\cap B_3)$$

$$P(A) = P(B_1)* P(A|B_1) + P(B_2)* P(A|B_2)+ P(B_3)* P(A|B_3)$$

We can extend this process to $n$ exhaustive events to get:

$$P(A) = \sum_{i=1}^nP(A\cap B_i)$$

$$P(A) = \sum_{i=1}^n P(B_i)* P(A|B_i)$$

This is the [law of total probability](https://en.wikipedia.org/wiki/Law_of_total_probability). The symbol $\sum$ tells us to take the sum of the iterative variables contained within it, iterating from the initial value written below, $i=1$, to the end value written above, $n$. As the number of variables grows, it becomes far more practical to write a sum in this format instead of writing out each instance separately. To illustrate the use of $\sum$, we can write $x_2+x_3+x_4= \sum_{i=2}^4 x_i$.

### Bayes' theorem
Let's now return to the **multiplication rule** for dependent events:

$$P(A\cap B) = P(B)*P(A|B)$$

By the same rule we also have the following equation:
$$P(B\cap A) = P(A)*P(B|A)$$

Since the probability of events $A$ and $B$ occuring together is the same regardless of in which order we write it, we have:

$$P(A\cap B) = P(B\cap A)$$

which means substituting the multiplication rule we have:
$$P(A)*P(B|A) = P(B)*P(A|B)$$

Rearranged we get:
$$P(B|A) = \frac{P(B)*P(A|B)}{P(A)}$$

From the law of total probability above we saw that we can write the total probability of $A$:
$$P(A) = \sum_{i=1}^n P(B_i)* P(A|B_i)$$

We can now rewrite our equation for $P(B|A)$ using the law of total probability:

$$P(B|A) = \frac{P(B)*P(A|B)}{\sum_{i=1}^n P(B_i)* P(A|B_i)}$$

We've just arrived at [Bayes' theorem](https://en.wikipedia.org/wiki/Bayes%27_theorem).


## An algorithm we can use

In many cases, we are interested in identifying which one of several possibilities is true by comparing their probabilities. This is what we plan on doing to categorize incoming messages as either "spam" or "ham." We are going to calculate the probability that an incoming message, $A$, is spam, $B_1$, or ham, $B_2$. Using the multiplication rule with a sample space that is exhaustive for $B_1$ and $B_2$ (since a message must be either spam or ham), we get:

$$P(B_1|A) = \frac{P(B_1)*P(A|B_1)}{P(A)}$$

$$P(B_2|A) = \frac{P(B_2)*P(A|B_2)}{P(A)}$$

We want to compare these two probabilities to know whether to classify a given event $A$ (a message) as $B_1$ or $B_2$ (spam or ham). When we divide one probability by the other to compare them, the common denominator $P(A)$ cancels out. For the purposes of comparing probabilities, therefore, we can ignore the denominator for faster calculations. This means we have:

$$P(B_1)|A) \propto P(B_1)*P(A|B_1)$$

$$P(B_2|A) \propto P(B_2)*P(A|B_2)$$

where $\propto$ is defined as "directly proportional to".

We are nearing the end of the derivation. We have just one assumption to make now for the use of the algorithm we want to apply. We're going to *assume* **conditional independence** of our events. In the context of a spam filter, this would mean that the words found in the messages appear completely independently from one another. We know this isn't true, and it's almost never true that events of interest are completely independent. But this assumption allows us to write a simple algorithm which can still work well for many real-world situations. Let's observe how this assumption plays out.

We know from above we have $P(B_1|A) \propto P(B_1)*P(A|B_1)$. $A$ is a message made up of a number of words $w_1,w_2,...,w_n$. We can rewrite $P(A)$ as the probability of the words that make of $A$: $P(w_1,w_2,...,w_n)$. Therefore the probabilities that a message is spam or ham given that the message is message $A$ are given by:

$$P(B_1|w_1,w_2,...,w_n) \propto P(B_1) * \prod_{i=1}^n P(w_i|B_1)$$

$$P(B_2|w_1,w_2,...,w_n) \propto P(B_2) * \prod_{i=1}^n P(w_i|B_2)$$

The $\prod$ symbol is the product equivalent of the sum symbol $\sum$.

What about when $P(w_i|B) = 0$? $P(w_i|B) = 0$ whenever the probability of a given word being spam or ham is zero? Since we're taking the product of probabilities, if any one of them is zero, the entire product goes to zero. This doesn't reflect the true probability. To correct for this, we use [additive smoothing](https://en.wikipedia.org/wiki/Additive_smoothing). We add a value called a smoothing parameter which we denote as $\alpha$ so that there are no zero values in the product. To keep all the probability values proportional, we need to use it for all cases. This looks like:

$$P(w_i|B) = \frac{N_{w_i|B} + \alpha}{N_{B} + \alpha \times N_{Vocabulary}}$$

where $N_{Vocabulary}$ is the number of unique words.



---
---
<a id='analysis_start'></a>
## Reading in the data
We'll now import our data and get started with the analysis. We'll take a look at the size of the data and explore the first few rows to familiarize ourselves with it.

In [1]:
# Import pandas library for data analysis.
import pandas as pd

# Read in the data.
messages = pd.read_csv('SMSSpamCollection.txt', sep='\t',header=None, names=['Label', 'SMS']) 
#tab-separated and no header row, add column names

# Display the number of rows and columns and first five rows to explore the data.
print("This data set contains {} rows and {} columns.".format(messages.shape[0], messages.shape[1]))
messages.head().style.hide_index()

This data set contains 5572 rows and 2 columns.


In [2]:
# What percentage of the messages are spam vs ham (aka not spam)?
round(100*messages['Label'].value_counts(normalize=True),1)
# Display values as percentages rounded to one decimal place.

ham     86.6
spam    13.4
Name: Label, dtype: float64

Upon exploration, we see that the messages are made up of alphanumeric characters and punctuation and written in English slang. 86.6% of the messages are real messages (ham), while the rest are spam.

## Setting aside unbiased data for testing

We'll split up the data into two sets - one for training the algorithm, the other for testing it. We want to do this split before we go any further to avoid creating a biased test. 80% of the data will go to training, the remaining 20% to testing. The testing data will be used to evaluate how the algorithm performs on messages with already known spam/non-spam values.

We want our filter to classify new messages with a greater than 80% accuracy.

To create the two sets, we'll start by randomizing the entire dataset using the `DataFrame.sample()` method.

In [3]:
# Randomize entire dataset.
messages_random = messages.sample(frac=1, random_state=1)
#frac parameter indicates proportion of set; random_state parameter allows reproducibility

# Reset the index of the randomized set.
messages_random.reset_index(drop=True, inplace=True)

# Save the first 80% as training set.
training = messages_random.copy().loc[:4457]

# Save the last 20% as testing set.
testing = messages_random.copy().loc[4457:]

# Reset the index of testing set.
testing.reset_index(drop=True, inplace=True)

# Check percentage of ham and spam in training set.
round(100*training['Label'].value_counts(normalize=True),1)

ham     86.5
spam    13.5
Name: Label, dtype: float64

In [4]:
# Check percentage of ham and spam in testing set.
round(100*testing['Label'].value_counts(normalize=True),1)

ham     86.8
spam    13.2
Name: Label, dtype: float64

After randomizing and then splitting the data into the two groups, I checked that the percentages of spam and ham values in both sets remained comparable to that of the original data. Their `value_counts` are output as percentages in the above two cells. All percentage values are within about 0.4%, so the data sets are comparable.

## Data cleaning

To be able to apply the Naive Bayes formula, the data needs to be formatted to be easy to work with. To accomplish this, we'll remove all the punctuation from the messages and switch to all lower case.

In [5]:
# Remove any non alpha-numeric characters, then switch to all lower case.
training['SMS'] = training['SMS'].str.replace(r'(\W)',' ').str.lower()

# Split strings into lists.
training['SMS'] = training['SMS'].str.split()

## Generating the vocabulary

Using the training set, we'll create a vocabulary of all unique words used in the messages.

In [6]:
# Create list of words in messages.
vocabulary = []
for msg in training['SMS']:
    for word in msg:
        vocabulary.append(word)

# Transform list to set to remove duplicates.        
set(vocabulary)
# Transform back to list.
list(vocabulary)
# Display first 10 words.
vocabulary[:10]

['yep',
 'by',
 'the',
 'pretty',
 'sculpture',
 'yes',
 'princess',
 'are',
 'you',
 'going']

## Assign frequency values

Next we'll generate a table of all the messages, the spam/ham assignments, and the frequency of vocabulary words in each message.

In [7]:
# Initialize dictionary of vocab words with values of 0 for length of training set.
word_counts_per_sms = {word: [0] * len(training['SMS']) for word in vocabulary}

# Iterate over index and sms content to count appearance of words.
for index, sms in enumerate(training['SMS']):
    for word in sms:
        word_counts_per_sms[word][index] += 1

# Transform word dictionary into dataframe.
training_words = pd.DataFrame(word_counts_per_sms)

# Concatenate with original set to have all data in the same dataframe.
training = pd.concat([training, training_words], axis=1)
training.head().style.hide_index()

## Creating the spam filter

With the vocabulary and assigned frequency table we created, we can now begin writing a filter function.


### Frequency table

We'll create a table of all the words in the vocabulary and how many times they show up in spam and ham messages. If a message contains a given word in the table, we can now calculate the probabilities that the message is spam and ham.

In [8]:
# Group data into spam and non-spam and get sums of groups.
word_count = training.groupby('Label').sum()

# Add column with sums of values in each row.
word_count['word_count'] = word_count.sum(axis=1)

# Display.
word_count

yep   by  the  pretty  sculpture  yes  princess  are   you  going  ...  \
Label                                                                     ...   
ham      9  110  920      12          1   65        24  337  1583    143  ...   
spam     0   34  157       0          0   16         0   64   255      3  ...   

       hides  secrets  n8  jewelry  related  trade  arul  bx526  wherre  \
Label                                                                     
ham        1        1   1        1        1      1     1      0       1   
spam       0        0   0        0        0      0     0      1       0   

       word_count  
Label              
ham         57237  
spam        15190  

[2 rows x 7784 columns]

### Probabilities

In [9]:
# Create Laplace smoothing variable and set equal to 1.
alpha = 1

# Set N_spam and N_ham from values calculated in table above.
N_spam = word_count['word_count']['spam']
N_ham = word_count['word_count']['ham']

# Set N_vocabulary as length of set of unique words in vocabulary.
N_vocabulary = len(set(vocabulary))

# Calculate P_spam and P_ham.
P_spam = training['Label'].value_counts(normalize=True)[1]
P_ham = training['Label'].value_counts(normalize=True)[0]

In [10]:
# Display the number of words in the vocabulary.
N_vocabulary

7783

### Calculations
Next we'll calculate $P(w_i|Spam)$ and $P(w_i|Ham)$ for each of the 7783 words in the vocabulary. We calculate the values beforehand so that when messages come in they can be instantly classifed rather than making calculations as messages come in.

We'll split the training data into separate groups for spam and ham. Then we'll create two dictionaries - one for spam words, the other for ham. We'll calculate the probability for each word that it appears in a spam or ham message and add the values to their respective dictionaries. This last step takes the longest processing time (around 20 seconds), but we only need to do it once. After the probability dictionaries are created, incoming messages can be processed quickly.

#### The math:

As derived above, the algorithm we're going to use is:

$$P(Spam|w_1,w_2,...,w_n)\propto P(Spam)\times\prod_{i=1}^n P(w_i|Spam)$$

$$P(Ham|w_1,w_2,...,w_n)\propto P(Ham)\times\prod_{i=1}^n P(w_i|Ham)$$

To calculate $P(w_i|Spam)$ and $P(w_i|Ham)$ in the above formulas:

$$P(w_i|Spam) = \frac{N_{w_i|Spam} + \alpha}{N_{Spam} + \alpha \times N_{Vocabulary}}$$

$$P(w_i|Ham) = \frac{N_{w_i|Ham} + \alpha}{N_{Ham} + \alpha \times N_{Vocabulary}}$$

* $N_{Spam}$ = number of words in all spam messages (not limited to unique words)
* $N_{Ham}$ = number of words in all non-spam messages (not limited to unique words)
* Use Laplace smoothing (aka add-one smoothing) so $\alpha = 1$.
* $N_{Vocabulary}$ = total number of unique words in all messages (spam and non-spam)

In [11]:
# Split the training data into separate groups for spam and ham.
training_spam = training[training['Label']=='spam']
training_ham = training[training['Label']=='ham']

In [12]:
# Initialize dictionaries of vocab words with values of 0 for lengths of sets.
P_w_spam = {word: [0] * len(training_spam['SMS']) for word in vocabulary}
P_w_ham = {word: [0] * len(training_ham['SMS']) for word in vocabulary}

# Iterate over vocabulary to calculate probability values and save to dictionaries.
for word in vocabulary:
    P_w_spam[word] = (training_spam[word].sum() + alpha) / (N_spam + alpha * N_vocabulary)
    P_w_ham[word] = (training_ham[word].sum() + alpha) / (N_ham + alpha * N_vocabulary)

### The filter function

Now we can create the spam filter which uses the equation above. The workflow of this filter will be:
1. Receive input message
2. Calculate $P(Spam|word)$ and $P(Ham|word)$
3. Compare the values in step 2
4. Classify message depending on which probability is greater. If probabilities are equal, request human classification.

After writing the function, we'll quickly test it on an obvious spam message and an obvious ham message to make sure it's working correctly.

In [13]:
# Import RE library for regular expressions.
import re

# Create a function that classifies incoming messages as spam or ham.
def classify(message):
    
    '''
    Clean incoming messages. Remove non
    alpha-numeric characters. Change to 
    lower case. Split the strings.
    '''
    message = re.sub('\W', ' ', message)
    message = message.lower()
    message = message.split()
    
    '''
    Calculate probabilities that message is 
    spam or ham given the words in the message.
    '''
    p_spam_given_message = P_spam
    p_ham_given_message = P_ham
    
    for word in message:
        if word in P_w_spam:
            p_spam_given_message *= P_w_spam[word]
        if word in P_w_ham:
            p_ham_given_message *= P_w_ham[word]
    '''
    Print probabilities.
    '''
    print('P(Spam|message):', p_spam_given_message)
    print('P(Ham|message):', p_ham_given_message)
    
    '''
    Print classification.
    '''
    if p_ham_given_message > p_spam_given_message:
        print('Label: Ham')
    elif p_ham_given_message < p_spam_given_message:
        print('Label: Spam')
    else:
        print('Equal probabilities, requires human classification.')

In [14]:
# Test function with obvious spam message.
classify('WINNER!! This is the secret code to unlock the money: C3421.')

P(Spam|message): 1.3481290211300841e-25
P(Ham|message): 1.9368049028589875e-27
Label: Spam


In [15]:
# Test function with obvious ham message.
classify("Sounds good, Tom, then see u there")

P(Spam|message): 2.4372375665888117e-25
P(Ham|message): 3.687530435009238e-21
Label: Ham


## Testing the spam filter on known data

We'll rewrite the filter function to return instead of print the classification. This way we can apply the function to the testing data set using `dataframe.apply(filter function)`. We'll save the returned results in a new column.

In [16]:
# Customize function for our test set: return instead of print label.
def classify_test_set(message):
    
    '''
    Clean incoming messages. Remove non
    alpha-numeric characters. Change to 
    lower case. Split the strings.
    '''
    message = re.sub('\W', ' ', message)
    message = message.lower()
    message = message.split()
    
    '''
    Calculate probabilities that message is 
    spam or ham given the words in the message.
    '''
    p_spam_given_message = P_spam
    p_ham_given_message = P_ham
    
    for word in message:
        if word in P_w_spam:
            p_spam_given_message *= P_w_spam[word]
        if word in P_w_ham:
            p_ham_given_message *= P_w_ham[word]
    '''
    Return classification.
    '''
    if p_ham_given_message > p_spam_given_message:
        return 'ham'
    elif p_ham_given_message < p_spam_given_message:
        return 'spam'
    else:
        return 'needs human classification'

In [17]:
# Apply the filter function to the test data and save results in new "predicted" column.
testing['predicted'] = testing['SMS'].apply(classify_test_set)

# Display the first 10 rows to explore the results.
testing.head(10).style.hide_index()

## Evaluating accuracy

We'll calculate the accuracy of the filter's performance using:<br>

accuracy = (number of correctly classified messages) / (total number of classified messages)

In [18]:
# Initialize variables.
correct = 0
total = testing['SMS'].count()

# Count correct values.
for index, row in testing.iterrows():
    if row['Label'] == row['predicted']:
        correct += 1
        
# Calculate accuracy.
correct / total

0.9874439461883409

## Conclusion

The spam filter we created using a Naive Bayes classifier algorithm was accurate in classifying text messages as spam or ham 98% of the time.

Although we made some practical assumptions to simplify the process, the filter still had a high degree of accuracy. This illustrates the merit of using even a simple probability algorithm to meaningfully classify data. The same technique could be applied to a large number of other scenarios such as filtering e-mail spam based on body content, designing a simplified ATS (applicant tracking system) for finding good job candidates, or sentiment analysis on political publications.